# This is my main project file. The data scraping, visualization and analysis will be done in this notebook. You can read more about the project in the report pdf found on my repository.

First, let's import the necessary libraries

In [293]:
import numpy as np
import pandas as pd
import folium 
import matplotlib.pyplot as plt
from urllib.request import urlopen
import geocoder
import requests
from geopy.geocoders import Nominatim
from IPython.display import clear_output
from sklearn.cluster import KMeans

In order to keep my Client id and secret secure, I will be reading them from a file saved on my computer that I will exclude from git. If you want to experiment with the notebook, you can create a free account of foursquare and repace CLIENT_ID and CLIENT_SECRET with your own and skip reading the file. Or you can write a txt file in the same folder as the notebook that has the CLIENT_ID on the first line and CLIENT_SECRET on the second. After making the .txt file, point to it in the client_cred variable. 

In [294]:
client_cred = 'foursquare_client_creds.txt'
file = open(client_cred, "r")
CLIENT_ID = file.readline()[:-1] #the [:-1] is used to cut out the '\n' character at the end of the line
CLIENT_SECRET = file.readline()
VERSION = '20180605' # Foursquare API version
geolocator = Nominatim(user_agent="neighborhood-recommender")

Let's try using foursquare to obtain results to make sure the connection was successful

In [295]:
lat = '40.1872'
lng = '44.5152'
radius = 500
LIMIT = 10
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)

# make the GET request
results = requests.get(url).json()["response"]['groups'][0]['items']
if results!=None:
    print("Connection was successful")
else:
    print("Something went wrong")

Connection was successful


## Now, let's scrape wikipedia pages for New York, Chicago and LA neighborhoods. 

# Chicago

In [357]:
Chicago_wiki_url = 'https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago'
NYC_wiki_url = 'https://en.wikipedia.org/wiki/Neighborhoods_in_New_York_City'
LA_wiki_url = 'https://en.wikipedia.org/wiki/List_of_districts_and_neighborhoods_of_Los_Angeles'

In [358]:
Chicago_neighborhoods = pd.read_html(Chicago_wiki_url, match='Woodlawn')[0]
Chicago_neighborhoods.drop(1, axis=1, inplace=True) #Drop the community area col
Chicago_neighborhoods.drop(0, axis=0, inplace=True) #Drop the first row that shouldve been the header
Chicago_neighborhoods.rename(columns = {0:'Neighborhood'}, inplace=True) #Rename the columns

In [359]:
#Get the latitude and longitude of the neighborhoods
geolocator = Nominatim(user_agent="neighborhood-recommender")
lats = []
longs = []
got_none = [] #the list of neighborhoods we got none for
got_none_ind = []
for i, neighb in enumerate(Chicago_neighborhoods['Neighborhood']):
    print(neighb)
    location = geolocator.geocode( neighb + ', Chicago')
    if location != None:
        lats.append(location.latitude)
        longs.append(location.longitude)
    else:
        got_none.append(neighb)
        got_none_ind.append(i)
        lats.append(np.nan)
        longs.append(np.nan)
    clear_output()

In [360]:
Chicago_neighborhoods['Latitude'] = lats
Chicago_neighborhoods['Longitude'] = longs

Sometimes geopy cant obtain latitude and longitude values. I explore those neighborhoods further below. Looks like a small change in the name can often fix the issue. If it doesnt work, I'll find the location manually or drop the row. 

In [361]:
print("List of neighborhoods with no location", got_none)

List of neighborhoods with no location ['Ashburn Estates', 'Belmont Heights', 'Cottage Grove Heights', 'Irving Woods', 'Jackson Park Highlands', 'Lakewood / Balmoral', 'Legends South (Robert Taylor Homes)', 'Margate Park', 'Polish Downtown', 'Ranch Triangle', "River's Edge", "Saint Ben's", 'Sheffield Neighbors', 'Sheridan Station Corridor', "Talley's Corner", 'Wacławowo', 'West Chesterfield', 'Wrightwood Neighbors']


In [362]:
#Drop the indices we got none for 
Chicago_neighborhoods.reset_index(inplace=True, drop=True)
Chicago_neighborhoods.drop(got_none_ind, inplace=True)
#Chicago_neighborhoods.reset_index(inplace=True, drop=True)

In [363]:
#Add some of the neighborhoods I could recover locations for
location = geolocator.geocode('Cottage Grove, Chicago')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood' : 'Cottage Grove' , 'Latitude' : location.latitude, 'Longitude' : location.longitude}, ignore_index=True)
location = geolocator.geocode('Jackson Park, Chicago')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood' : 'Jackson Park' , 'Latitude' : location.latitude, 'Longitude' : location.longitude}, ignore_index=True)
location = geolocator.geocode('Lakewood, Chicago')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood' : 'Lakewood' , 'Latitude' : location.latitude, 'Longitude' : location.longitude}, ignore_index=True)
location = geolocator.geocode('Balmoral, Chicago')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood' : 'Balmoral' , 'Latitude' : location.latitude, 'Longitude' : location.longitude}, ignore_index=True)
location = geolocator.geocode('Wrightwood, Chicago')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood' : 'Wrightwood' , 'Latitude' : location.latitude, 'Longitude' : location.longitude}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods.sort_values(by='Neighborhood')
Chicago_neighborhoods = Chicago_neighborhoods.reset_index(drop=True)

In [364]:
Chicago_neighborhoods.head()

Neighborhood   Latitude  Longitude
0      Albany Park  41.971937 -87.716174
1  Altgeld Gardens  41.654864 -87.600446
2    Andersonville  41.977139 -87.669273
3   Archer Heights  41.811422 -87.726165
4    Armour Square  41.840033 -87.633107

In [365]:
Chicago_neighborhoods.shape

(233, 3)

In [366]:
chi_location = geolocator.geocode('Chicago, IL')

In [367]:
# create map of Toronto using latitude and longitude values
map_chicago = folium.Map(location=[chi_location.latitude, chi_location.longitude], zoom_start=10)
for lat, lng, neighborhood in zip(Chicago_neighborhoods['Latitude'], Chicago_neighborhoods['Longitude'], Chicago_neighborhoods['Neighborhood']):
    label = '{}, Chicago'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chicago)  
    
map_chicago

## When we zoom in, we can see that some of the neighborhoods are not actually in Chicago. This is either a result of geopy's errors or a mistake from scraping neighborhood names. I'm fixing that below. 

I did so by going through the map and checking out the neighborhoods outside of chicago one by one. Some of them were just duplicated of neighborhoods with slightly different names or were names of residential properties instead of neighborhoods. Those I dropped. The others I got the location of by doing a google search or specifying the address more properly.

In [368]:
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Central Station']

In [369]:
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'River North']
loc = geolocator.geocode('River North, Chicago, IL, USA')
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'River North', 'Latitude': loc.latitude, 'Longitude': loc.longitude}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'University Village']
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Old Town Triangle']
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'K-Town']
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Lincoln Square']
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'Lincoln Square', 'Latitude': 41.976049, 'Longitude': -87.7079486}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Heart of Chicago']
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Big Oaks']
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'Big Oaks', 'Latitude': 41.9992963, 'Longitude': -87.7540899}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Chrysler Village']
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'Chrysler Village', 'Latitude': 41.7800088, 'Longitude': -87.7405553}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Old Town']
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'Old Town', 'Latitude': 41.9111221, 'Longitude': -87.6492029}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Fifth City']
Chicago_neighborhoods = Chicago_neighborhoods.append({'Neighborhood': 'Fifth City', 'Latitude': 41.8776055, 'Longitude': -87.7152837}, ignore_index=True)
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'New Eastside']
Chicago_neighborhoods = Chicago_neighborhoods[Chicago_neighborhoods.Neighborhood != 'Museum Campus']
Chicago_neighborhoods = Chicago_neighborhoods.sort_values(by='Neighborhood')
Chicago_neighborhoods.reset_index(drop=True, inplace=True)

In [370]:
Chicago_neighborhoods.head()

Neighborhood   Latitude  Longitude
0      Albany Park  41.971937 -87.716174
1  Altgeld Gardens  41.654864 -87.600446
2    Andersonville  41.977139 -87.669273
3   Archer Heights  41.811422 -87.726165
4    Armour Square  41.840033 -87.633107

# Let's try this again. 

In [372]:
# create map of Toronto using latitude and longitude values
map_chicago = folium.Map(location=[chi_location.latitude, chi_location.longitude], zoom_start=10)
for lat, lng, neighborhood in zip(Chicago_neighborhoods['Latitude'], Chicago_neighborhoods['Longitude'], Chicago_neighborhoods['Neighborhood']):
    label = '{}, Chicago'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chicago)  
    
map_chicago

In [373]:
Chicago_neighborhoods.to_csv('Chicago_neighborhoods.csv')

# NYC

In [374]:
NYC = pd.read_html(NYC_wiki_url, match='Arrochar')[0]
NYC.drop([0,1,2,3], axis=1, inplace=True)
NYC.drop([0,60], axis=0, inplace=True)
NYC_neighborhoods = pd.DataFrame(columns=['Neighborhood'])
NYC_neighborhoods

Empty DataFrame
Columns: [Neighborhood]
Index: []

In [375]:
for n in NYC[4]:
    neighbs = n.split(',')
    for nb in neighbs:
        NYC_neighborhoods = NYC_neighborhoods.append({'Neighborhood': nb.strip()}, ignore_index=True)

In [376]:
NYC_neighborhoods.sort_values(by='Neighborhood', inplace=True)
NYC_neighborhoods.reset_index(drop=True, inplace=True)

In [377]:
lats = []
longs = []
got_none = [] #the list of neighborhoods we got none for
got_none_ind = []
for i, neighb in enumerate(NYC_neighborhoods['Neighborhood']):
    print(neighb)
    location = geolocator.geocode( neighb + ', NYC')
    if location != None:
        lats.append(location.latitude)
        longs.append(location.longitude)
    else:
        got_none.append(neighb)
        got_none_ind.append(i)
        lats.append(np.nan)
        longs.append(np.nan)
    clear_output()

In [378]:
NYC_neighborhoods['Latitude'] = lats
NYC_neighborhoods['Longitude'] = longs

In [379]:
print("List of neighborhoods with no location", got_none)

List of neighborhoods with no location ['Greenwood Heights', 'Hilltop Village', 'Kew Gardens Hills', 'Meiers Corners', 'Plum Beach', 'Prospect Lefferts Gardens', 'Van Cortlandt Village']


In [380]:
print(NYC_neighborhoods.shape)
NYC_neighborhoods.drop(got_none_ind, inplace=True, axis=0)
print(NYC_neighborhoods.shape)

(328, 3)
(321, 3)


In [381]:
NYC_neighborhoods.reset_index(drop=True, inplace=True)

In [382]:
#removing duplicates
NYC_neighborhoods = NYC_neighborhoods.groupby('Neighborhood').first().reset_index()

In [383]:
NYC_neighborhoods.shape

(305, 3)

In [384]:
NYC_neighborhoods.to_csv('NYC_neighborhoods.csv')

In [385]:
nyc_location = geolocator.geocode('NYC, NY')

In [589]:
# create map of Toronto using latitude and longitude values
map_nyc = folium.Map(location=[nyc_location.latitude, nyc_location.longitude], zoom_start=10)
for lat, lng, neighborhood in zip(NYC_neighborhoods['Latitude'], NYC_neighborhoods['Longitude'], NYC_neighborhoods['Neighborhood']):
    label = '{}, NYC'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_nyc)  
    
map_nyc

## Same as before, cleaning out the neighborhoods that arent actually in New York

In [390]:
drop = ['Indian Village', 'Mount Hope']
geolocator.geocode('Indian Village, New York City, New York, USA')
for n in drop:
    NYC_neighborhoods = NYC_neighborhoods[NYC_neighborhoods.Neighborhood != n]
NYC_neighborhoods = NYC_neighborhoods[NYC_neighborhoods.Neighborhood != 'New Hyde Park']
NYC_neighborhoods = NYC_neighborhoods.append({'Neighborhood': 'New Hyde Park', 'Latitude': 40.7326609, 'Longitude': -73.6948062}, ignore_index=True)
NYC_neighborhoods = NYC_neighborhoods.sort_values(by='Neighborhood')
NYC_neighborhoods.reset_index(drop=True, inplace=True)

In [391]:
NYC_neighborhoods.head()

Neighborhood   Latitude  Longitude
0       Allerton  40.866111 -73.850556
1  Alphabet City  40.725102 -73.979583
2       Annadale  40.544550 -74.176532
3  Arden Heights  40.557629 -74.188609
4      Arlington  40.632326 -74.165144

In [393]:
# create map of Toronto using latitude and longitude values
map_nyc = folium.Map(location=[nyc_location.latitude, nyc_location.longitude], zoom_start=10)
for lat, lng, neighborhood in zip(NYC_neighborhoods['Latitude'], NYC_neighborhoods['Longitude'], NYC_neighborhoods['Neighborhood']):
    label = '{}, NYC'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_nyc)  
    
map_nyc

In [404]:
print('NYC, ', NYC_neighborhoods.shape)
print('Chicago, ', Chicago_neighborhoods.shape)

NYC,  (303, 3)
Chicago,  (226, 3)


# Now that we have the list of neighborhoods and their locations, it's time for some feature extraction.

### First we make a dataframes with venues 

In [453]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [454]:
def getNearbyVenues(names, latitudes, longitudes):
    radius = 2000
    LIMIT = 500
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
        clear_output()

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [455]:
NYC_venues = getNearbyVenues(names=NYC_neighborhoods['Neighborhood'],
                   latitudes=NYC_neighborhoods['Latitude'],
                   longitudes=NYC_neighborhoods['Longitude']
                  )


In [456]:
NYC_venues['Neighborhood'] = NYC_venues['Neighborhood'] + ', NYC'
NYC_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Allerton, NYC              40.866111              -73.850556   
1  Allerton, NYC              40.866111              -73.850556   
2  Allerton, NYC              40.866111              -73.850556   
3  Allerton, NYC              40.866111              -73.850556   
4  Allerton, NYC              40.866111              -73.850556   

                  Venue  Venue Latitude  Venue Longitude      Venue Category  
0     Sal & Doms Bakery       40.865377       -73.855236        Dessert Shop  
1           Nicks Pizza       40.870352       -73.846171         Pizza Place  
2            Fratelli's       40.863019       -73.843607  Italian Restaurant  
3  Gun Hill Brewing Co.       40.872139       -73.855698             Brewery  
4    Four Seasons Nails       40.869402       -73.844527                 Spa

In [457]:
Chicago_venues = getNearbyVenues(names=Chicago_neighborhoods['Neighborhood'],
                   latitudes=Chicago_neighborhoods['Latitude'],
                   longitudes=Chicago_neighborhoods['Longitude']
                  )


In [458]:
Chicago_venues['Neighborhood'] = Chicago_venues['Neighborhood'] + ', Chicago'
Chicago_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Albany Park, Chicago              41.971937              -87.716174   
1  Albany Park, Chicago              41.971937              -87.716174   
2  Albany Park, Chicago              41.971937              -87.716174   
3  Albany Park, Chicago              41.971937              -87.716174   
4  Albany Park, Chicago              41.971937              -87.716174   

                          Venue  Venue Latitude  Venue Longitude  \
0    Cairo Nights Hookah Lounge       41.975776       -87.715547   
1                    Tre Kronor       41.975842       -87.711037   
2                     Nighthawk       41.967974       -87.713415   
3  Great Sea Chinese Restaurant       41.968496       -87.710678   
4     Popeyes Louisiana Kitchen       41.968459       -87.713156   

            Venue Category  
0               Hookah Bar  
1  Scandinavian Restaurant  
2             Cocktail Bar  
3       Chinese Restaurant  
4      Fried Chicken Joint

In [459]:
# Putting all the venues together
Venues = pd.concat([NYC_venues, Chicago_venues])
Venues.reset_index(drop=True, inplace=True)

In [460]:
# one hot encoding
onehot = pd.get_dummies(Venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
onehot['City, Neighborhood'] = Venues['Neighborhood'] 

In [461]:
columns = onehot.columns.tolist()
columns.remove('City, Neighborhood')
columns.insert(0, 'City, Neighborhood')

In [462]:
onehot = onehot.loc[:, columns]

In [463]:
onehot.head()

City, Neighborhood  ATM  Accessories Store  Adult Boutique  \
0      Allerton, NYC    0                  0               0   
1      Allerton, NYC    0                  0               0   
2      Allerton, NYC    0                  0               0   
3      Allerton, NYC    0                  0               0   
4      Allerton, NYC    0                  0               0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  0                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   

   Airport Gate  Airport Lounge     ...       Weight Loss Center  Whisky Bar  \
0             0               0     ...                        0           0   
1             0               0     ...                        0           0   
2             0               0     ...                        0           0   
3             0               0     ...                        0           0   
4             0               0     ...                        0           0   

   Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0         0          0       0            0              0            0    0   
1         0          0       0            0              0            0    0   
2         0          0       0            0              0            0    0   
3         0          0       0            0              0            0    0   
4         0          0       0            0              0            0    0   

   Zoo Exhibit  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 487 columns]

In [464]:
Venues_grouped = onehot.groupby('City, Neighborhood').sum().reset_index()

In [465]:
Venues_grouped.head()

City, Neighborhood  ATM  Accessories Store  Adult Boutique  \
0      Albany Park, Chicago    0                  0               0   
1             Allerton, NYC    0                  0               0   
2        Alphabet City, NYC    0                  0               0   
3  Altgeld Gardens, Chicago    0                  0               0   
4    Andersonville, Chicago    0                  0               0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  1                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   

   Airport Gate  Airport Lounge     ...       Weight Loss Center  Whisky Bar  \
0             0               0     ...                        0           0   
1             0               0     ...                        0           0   
2             0               0     ...                        0           0   
3             0               0     ...                        0           0   
4             0               0     ...                        0           1   

   Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0         0          0       0            1              0            1    0   
1         0          0       0            0              0            0    0   
2         0          2       0            0              0            4    0   
3         1          0       0            0              0            0    0   
4         0          1       0            0              0            0    0   

   Zoo Exhibit  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 487 columns]

In [466]:
# Saving this dataframe for convenience. Later I won't need to rerun the code to get to it 
Venues_grouped.to_csv('Venues_grouped.csv')

## Some of the categories are very specific (e.g. cafe and coffee shop). Below, I merge a few of them together to get better features

In [467]:
Venues_grouped = pd.read_csv('Venues_grouped.csv', header=0, index_col = 0)

In [468]:
categories = Venues_grouped.columns.tolist()[1:]
print(*categories, sep='\n')

ATM
Accessories Store
Adult Boutique
Afghan Restaurant
African Restaurant
Airport
Airport Food Court
Airport Gate
Airport Lounge
Airport Service
Airport Terminal
American Restaurant
Amphitheater
Animal Shelter
Antique Shop
Aquarium
Arcade
Arepa Restaurant
Argentinian Restaurant
Art Gallery
Art Museum
Arts & Crafts Store
Arts & Entertainment
Asian Restaurant
Athletics & Sports
Auditorium
Australian Restaurant
Austrian Restaurant
Auto Garage
Auto Workshop
Automotive Shop
BBQ Joint
Baby Store
Bagel Shop
Bakery
Bank
Bar
Baseball Field
Baseball Stadium
Basketball Court
Basketball Stadium
Bath House
Bavarian Restaurant
Beach
Beach Bar
Bed & Breakfast
Beer Bar
Beer Garden
Beer Store
Big Box Store
Bike Rental / Bike Share
Bike Shop
Bike Trail
Bistro
Board Shop
Boat or Ferry
Bookstore
Border Crossing
Botanical Garden
Boutique
Bowling Alley
Boxing Gym
Brazilian Restaurant
Breakfast Spot
Brewery
Bridge
Bubble Tea Shop
Buffet
Building
Burger Joint
Burmese Restaurant
Burrito Place
Bus Line
Bus Stat

In [469]:
def join_features(list_to_join, new_name, df):
    df['temp_name'] = df[list_to_join].sum(axis=1)
    df = df.drop(columns=list_to_join)
    df = df.rename(columns={'temp_name': new_name})
    return df

In [470]:
Venues_grouped = join_features(['Wine Bar', 'Wine Shop'], 'Wine', Venues_grouped)

In [471]:
Venues_grouped = join_features(['Airport Food Court', 'Airport Lounge', 'Airport Service', 'Airport Terminal'], 'Airport', Venues_grouped)

In [472]:
Venues_grouped = join_features(['Art Gallery', 'Art Museum', 'Performing Arts Venue', 'Public Art', 'Street Art'], 'Art', Venues_grouped)

In [473]:
Venues_grouped = join_features(['Baseball Field', 'Baseball Stadium'], 'Baseball', Venues_grouped)
Venues_grouped = join_features(['Basketball Court', 'Basketball Stadium'], 'Basketball', Venues_grouped)
Venues_grouped = join_features(['Beer Bar', 'Beer Garden', 'Brewery'], 'Beer', Venues_grouped)
Venues_grouped = join_features(['Bike Rental / Bike Share', 'Bike Shop'], 'Bike Shop', Venues_grouped)
Venues_grouped = join_features(['Bus Station', 'Bus Stop'], 'Bus Stop', Venues_grouped)
Venues_grouped = join_features(['Café', 'Coffee Shop'], 'Cofee', Venues_grouped)
Venues_grouped = join_features(['Soccer Field', 'Soccer Stadium'], 'Soccer', Venues_grouped)
Venues_grouped = join_features(['Tennis Court', 'Tennis Stadium'], 'Tennis', Venues_grouped)
Venues_grouped = join_features(['Zoo', 'Zoo Exhibit'], 'Zoo', Venues_grouped)


In [474]:
#Sorting the columns
columns = Venues_grouped.columns.tolist()
columns.remove('City, Neighborhood')
columns.sort()
columns.insert(0, 'City, Neighborhood')
Venues_grouped = Venues_grouped.loc[:, columns]

In [475]:
Venues_grouped.shape

(528, 471)

# K-means 

In [476]:
kclusters = 10

Venues_grouped_clustering = Venues_grouped.drop('City, Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Venues_grouped_clustering)
kmeans.labels_[0:50] 

array([7, 5, 0, 1, 6, 5, 8, 1, 1, 1, 5, 1, 1, 6, 4, 6, 4, 7, 7, 4, 2, 0,
       5, 5, 0, 5, 1, 5, 6, 1, 5, 7, 5, 1, 5, 6, 6, 6, 5, 5, 5, 8, 8, 8,
       1, 1, 6, 5, 6, 6])

In [477]:
%%capture
Clusters_of_neighborhoods = Venues_grouped[['City, Neighborhood']]
Clusters_of_neighborhoods['Cluster label'] = kmeans.labels_
temp_df = Venues.groupby('Neighborhood').mean().reset_index()
Clusters_of_neighborhoods['Latitude'] = temp_df[['Neighborhood Latitude']]
Clusters_of_neighborhoods['Longitude'] = temp_df[['Neighborhood Longitude']]



In [478]:
Clusters_of_neighborhoods.head()

City, Neighborhood  Cluster label   Latitude  Longitude
0      Albany Park, Chicago              7  41.971937 -87.716174
1             Allerton, NYC              5  40.866111 -73.850556
2        Alphabet City, NYC              0  40.725102 -73.979583
3  Altgeld Gardens, Chicago              1  41.654864 -87.600446
4    Andersonville, Chicago              6  41.977139 -87.669273

In [479]:
cmap = {0: 'red', 1: 'green', 2: 'yellow', 3: 'blue', 4: 'black', 5: 'white', 6: 'lightsteelblue', 7: 'lime', 8: 'deeppink', 9: 'purple', 10: 'plum'}
colors_array = [cmap[x] for x in Clusters_of_neighborhoods['Cluster label']]

# The map below shows the clusters. This is a good tool for freely exploring the neighborhoods. The ones with the same colors are likely to be similar. Zoom to explore

In [590]:
# create map
latitude = Clusters_of_neighborhoods['Latitude'].mean()
longitude = Clusters_of_neighborhoods['Longitude'].mean()
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=6)

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Clusters_of_neighborhoods['Latitude'], Clusters_of_neighborhoods['Longitude'], Clusters_of_neighborhoods['City, Neighborhood'], Clusters_of_neighborhoods['Cluster label']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=cmap[cluster],
        fill=True,
        fill_color=cmap[cluster],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## While this is a good tool for freely comparing the neighborhoods, what if I'm specifically interested in finding the neighborhoods most similar to the ones I like? We can use a content based recommender for that. We will use the cosine similarity metric between neighborhoods to give most similar neighborhoods to the ones of interest.  

# Content Based Recommender

In [481]:
from sklearn.metrics.pairwise import cosine_similarity

In [485]:
matrix = Venues_grouped_clustering.values
cosine_matrix = cosine_similarity(matrix)

In [490]:
cosine_matrix

array([[1.        , 0.46571506, 0.46408228, ..., 0.52071918, 0.47140452,
        0.37798038],
       [0.46571506, 1.        , 0.44581105, ..., 0.54699922, 0.57516521,
        0.48382573],
       [0.46408228, 0.44581105, 1.        , ..., 0.30418306, 0.53956374,
        0.58909764],
       ...,
       [0.52071918, 0.54699922, 0.30418306, ..., 1.        , 0.36401992,
        0.32133306],
       [0.47140452, 0.57516521, 0.53956374, ..., 0.36401992, 1.        ,
        0.63998275],
       [0.37798038, 0.48382573, 0.58909764, ..., 0.32133306, 0.63998275,
        1.        ]])

In [493]:
Similarity =pd.DataFrame(data= cosine_matrix, columns=Venues_grouped['City, Neighborhood'])

In [495]:
Similarity.index = Venues_grouped['City, Neighborhood']

In [498]:
Similarity.head()

City, Neighborhood        Albany Park, Chicago  Allerton, NYC  \
City, Neighborhood                                              
Albany Park, Chicago                  1.000000       0.465715   
Allerton, NYC                         0.465715       1.000000   
Alphabet City, NYC                    0.464082       0.445811   
Altgeld Gardens, Chicago              0.201843       0.126428   
Andersonville, Chicago                0.604346       0.390372   

City, Neighborhood        Alphabet City, NYC  Altgeld Gardens, Chicago  \
City, Neighborhood                                                       
Albany Park, Chicago                0.464082                  0.201843   
Allerton, NYC                       0.445811                  0.126428   
Alphabet City, NYC                  1.000000                  0.176863   
Altgeld Gardens, Chicago            0.176863                  1.000000   
Andersonville, Chicago              0.444500                  0.121854   

City, Neighborhood        Andersonville, Chicago  Annadale, NYC  \
City, Neighborhood                                                
Albany Park, Chicago                    0.604346       0.421637   
Allerton, NYC                           0.390372       0.677098   
Alphabet City, NYC                      0.444500       0.418042   
Altgeld Gardens, Chicago                0.121854       0.152318   
Andersonville, Chicago                  1.000000       0.333333   

City, Neighborhood        Archer Heights, Chicago  Arden Heights, NYC  \
City, Neighborhood                                                      
Albany Park, Chicago                     0.422816            0.483046   
Allerton, NYC                            0.500030            0.686772   
Alphabet City, NYC                       0.281322            0.415705   
Altgeld Gardens, Chicago                 0.156326            0.113961   
Andersonville, Chicago                   0.293355            0.378244   

City, Neighborhood        Arlington, NYC  Armour Square, Chicago  \
City, Neighborhood                                                 
Albany Park, Chicago            0.341802                0.611871   
Allerton, NYC                   0.490630                0.458570   
Alphabet City, NYC              0.231193                0.375688   
Altgeld Gardens, Chicago        0.118835                0.072871   
Andersonville, Chicago          0.221863                0.466052   

City, Neighborhood             ...        Windsor Terrace, NYC  Wingate, NYC  \
City, Neighborhood             ...                                             
Albany Park, Chicago           ...                    0.560541      0.360894   
Allerton, NYC                  ...                    0.412933      0.540971   
Alphabet City, NYC             ...                    0.577663      0.385027   
Altgeld Gardens, Chicago       ...                    0.261991      0.122839   
Andersonville, Chicago         ...                    0.515053      0.339760   

City, Neighborhood        Woodhaven, NYC  Woodlawn, Chicago  Woodlawn, NYC  \
City, Neighborhood                                                           
Albany Park, Chicago            0.425418           0.566423       0.329846   
Allerton, NYC                   0.696972           0.366508       0.733269   
Alphabet City, NYC              0.296743           0.445533       0.343061   
Altgeld Gardens, Chicago        0.095083           0.218103       0.041902   
Andersonville, Chicago          0.224552           0.448261       0.171170   

City, Neighborhood        Woodrow, NYC  Woodside, NYC  Wrightwood, Chicago  \
City, Neighborhood                                                           
Albany Park, Chicago          0.449560       0.425762             0.520719   
Allerton, NYC                 0.691403       0.333354             0.546999   
Alphabet City, NYC            0.342672       0.310891             0.304183   
Altgeld Gardens, Chicago      0.159091       0.079900             0.

# Now, in order to see most similar neighborhoods, all we have to do is pick a row (or a column) and sort the values. 

For instance, I really like Wicker Park in Chicago

In [503]:
ranked = Similarity[['Wicker Park, Chicago']].sort_values(by='Wicker Park, Chicago')[::-1]

This is the list of neighborhoods in both Chicago and New York that are similar to it.

In [505]:
ranked

City, Neighborhood                         Wicker Park, Chicago
City, Neighborhood                                             
Wicker Park, Chicago                                   1.000000
Bucktown, Chicago                                      0.933411
Pulaski Park, Chicago                                  0.835827
West Town, Chicago                                     0.809142
Noble Square, Chicago                                  0.773122
Nortown, Chicago                                       0.761478
Ukrainian Village, Chicago                             0.710407
Graceland West, Chicago                                0.693046
Lake View, Chicago                                     0.668332
Lake View East, Chicago                                0.668332
Lakewood, Chicago                                      0.668022
Wrigleyville, Chicago                                  0.659925
West Lakeview, Chicago                                 0.656042
Buena Park, Chicago                                    0.656042
Goose Island, Chicago                                  0.655876
West DePaul, Chicago                                   0.653183
North Center, Chicago                                  0.650693
Bedford-Stuyvesant, NYC                                0.647148
Stuyvesant Heights, NYC                                0.644714
Little Italy, NYC                                      0.638524
Chinatown, NYC                                         0.635123
Roscoe Village, Chicago                                0.634494
Smith Park, Chicago                                    0.632426
Greenpoint, NYC                                        0.630176
Fish Bay, NYC                                          0.627133
Clinton Hill, NYC                                      0.627115
Mott Haven, NYC                                        0.626850
Boystown, Chicago                                      0.625051
Steinway, NYC                                          0.620782
Glendale, NYC                                          0.619521
Greenwich Village, NYC                                 0.619445
Ravenswood Manor, Chicago                              0.618479
Long Island City, NYC                                  0.617895
Bowmanville, Chicago                                   0.614837
Merchant Park, Chicago                                 0.612381
Kosciuszko Park, Chicago                               0.612039
Palmer Square, Chicago                                 0.610839
Logan Square, Chicago                                  0.610759
Rosehill, Chicago                                      0.607927
Parkview, Chicago                                      0.604529
Park Slope, NYC                                        0.604248
Williamsburg, NYC                                      0.600950
Livingston, NYC                                        0.598592
East Flushing, NYC                                     0.597138
Old Norwood, Chicago                                   0.596913
East Village, NYC                                      0.595754
Belmont Terrace, Chicago                               0.595579
Belmont Gardens, Chicago                               0.595579
Belmont Central, Chicago                               0.595579
Hunters Point, NYC                                     0.594671
Ditmars, NYC                                           0.594570
Weeksville, NYC                                        0.594165
Spanish Harlem, NYC                                    0.593264
Humboldt Park, Chicago                                 0.591476
West Humboldt Park, Chicago                            0.591476
SoHo, NYC                                              0.590802
Avondale Gardens, Chicago                              0.590772
Avondale, Chicago                                      0.590772
Jackowo, Chicago                                       0.590772
Ravenswood Gardens, Chicago                            0.590132
Crown Heights, NYC              

Let's filter it to just show the neighborhoods in New York. 

In [518]:
ranked[['NYC' in x for x in ranked.index]]

City, Neighborhood         Wicker Park, Chicago
City, Neighborhood                             
Bedford-Stuyvesant, NYC                0.647148
Stuyvesant Heights, NYC                0.644714
Little Italy, NYC                      0.638524
Chinatown, NYC                         0.635123
Greenpoint, NYC                        0.630176
Fish Bay, NYC                          0.627133
Clinton Hill, NYC                      0.627115
Mott Haven, NYC                        0.626850
Steinway, NYC                          0.620782
Glendale, NYC                          0.619521
Greenwich Village, NYC                 0.619445
Long Island City, NYC                  0.617895
Park Slope, NYC                        0.604248
Williamsburg, NYC                      0.600950
Livingston, NYC                        0.598592
East Flushing, NYC                     0.597138
East Village, NYC                      0.595754
Hunters Point, NYC                     0.594671
Ditmars, NYC                           0.594570
Weeksville, NYC                        0.594165
Spanish Harlem, NYC                    0.593264
SoHo, NYC                              0.590802
Crown Heights, NYC                     0.590119
Yorkville, NYC                         0.589775
Fort Hamilton, NYC                     0.588554
Bushwick, NYC                          0.583333
Ocean Hill, NYC                        0.581588
West Village, NYC                      0.580019
NoHo, NYC                              0.579578
Fresh Pond, NYC                        0.577568
Carroll Gardens, NYC                   0.577539
Fort Greene, NYC                       0.575320
Lower East Side, NYC                   0.574271
Boerum Hill, NYC                       0.574032
Sunnyside, NYC                         0.573840
Kew Gardens, NYC                       0.573629
Bay Ridge, NYC                         0.571684
East Harlem, NYC                       0.571501
Forest Hills, NYC                      0.568607
Two Bridges, NYC                       0.567701
Hamilton Heights, NYC                  0.567206
Bronx River, NYC                       0.565600
Fieldston, NYC                         0.564573
Alphabet City, NYC                     0.563382
Randall's Island, NYC                  0.562804
Bensonhurst, NYC                       0.559563
Bayside, NYC                           0.559100
Madison, NYC                           0.558481
Oakland Gardens, NYC                   0.558287
Kingsbridge, NYC                       0.557626
Marble Hill, NYC                       0.557487
Red Hook, NYC                          0.555273
Spuyten Duyvil, NYC                    0.554118
Morris Park, NYC                       0.553786
Brooklyn Navy Yard, NYC                0.552864
Sunset Park, NYC                       0.551941
Gowanus, NYC                           0.546365
Wards Island, NYC                      0.544694
Maspeth, NYC                           0.544591
Windsor Terrace, NYC                   0.544412
Linden Hill, NYC                       0.542987
Pelham Bay, NYC                        0.542594
Pelham Gardens, NYC                    0.542594
Kensington, NYC                        0.541812
Baychester, NYC                        0.541609
Kingsbridge Heights, NYC               0.540329
Riverdale, NYC                         0.539564
Pelham Parkway, NYC                    0.536587
Waterside Plaza, NYC                   0.536290
Ridgewood, NYC                         0.535923
Fulton Mall, NYC                       0.534085
University Heights, NYC                0.530341
Westchester Square, NYC                0.527321
Middle Village, NYC                    0.526861
Stuyvesant Town, NYC                   0.526487
Cobble Hill, NYC                       0.524017
Throgs Neck, NYC                       0.522855
Ravenswood, NYC                        0.522303
Greenridge, NYC                        0.522223
Borough Park, NYC                      0.520686
Brooklyn Heights, NYC                  0.520412
Bedford Park, NY

Now, let's do this for a few other neighborhoods and google the results to see if they make sense. 

In [520]:
neighborhood = 'South Loop, Chicago'
ranked = Similarity[[neighborhood]].sort_values(by=neighborhood)[::-1]
ranked[['NYC' in x for x in ranked.index]]

City, Neighborhood         South Loop, Chicago
City, Neighborhood                            
Highbridge, NYC                       0.558501
Farragut, NYC                         0.558049
Livingston, NYC                       0.543510
Rego Park, NYC                        0.531457
University Heights, NYC               0.527679
Brooklyn Heights, NYC                 0.525431
Dumbo, NYC                            0.521641
Mott Haven, NYC                       0.519213
Morris Park, NYC                      0.518224
Queensboro Hill, NYC                  0.516574
Vinegar Hill, NYC                     0.514994
Middle Village, NYC                   0.514399
Pelham Bay, NYC                       0.513948
Pelham Gardens, NYC                   0.513948
Upper West Side, NYC                  0.513429
Fulton Ferry, NYC                     0.513236
Pelham Parkway, NYC                   0.512742
Kingsbridge Heights, NYC              0.510595
Kew Gardens, NYC                      0.509618
Huguenot, NYC                         0.508608
Forest Hills, NYC                     0.505120
Waterside Plaza, NYC                  0.503921
Hollis Hills, NYC                     0.503062
Polo Grounds, NYC                     0.495985
Morningside Heights, NYC              0.495469
Brooklyn Navy Yard, NYC               0.494782
Cunningham Heights, NYC               0.494291
Queensbridge, NYC                     0.493728
Bronx River, NYC                      0.490990
Kingsbridge, NYC                      0.490556
Allerton, NYC                         0.488285
East Harlem, NYC                      0.486880
West Village, NYC                     0.486864
Fish Bay, NYC                         0.485525
Beechhurst, NYC                       0.485066
Washington Heights, NYC               0.483087
Concourse, NYC                        0.482530
Spuyten Duyvil, NYC                   0.480978
Manhattanville, NYC                   0.480538
Fort Greene, NYC                      0.480233
Laconia, NYC                          0.480173
Fulton Mall, NYC                      0.479857
Woodrow, NYC                          0.478544
Fieldston, NYC                        0.477191
Marble Hill, NYC                      0.476281
Financial District, NYC               0.475248
Tribeca, NYC                          0.472796
Harlem, NYC                           0.472714
Melrose, NYC                          0.472103
Two Bridges, NYC                      0.472045
Battery Park City, NYC                0.471698
Manhattan Valley, NYC                 0.471545
Egbertville, NYC                      0.469895
Spanish Harlem, NYC                   0.469251
Long Island City, NYC                 0.467437
Sheepshead Bay, NYC                   0.465491
Liberty Park, NYC                     0.465417
Cobble Hill, NYC                      0.465129
Riverdale, NYC                        0.462910
Midwood, NYC                          0.462699
Stuyvesant Town, NYC                  0.461560
Garden Bay, NYC                       0.460590
Mill Island, NYC                      0.460590
Alphabet City, NYC                    0.460442
Rose Hill, NYC                        0.460255
Rosebank, NYC                         0.456982
Claremont, NYC                        0.456908
Morris Heights, NYC                   0.456880
Concourse Village, NYC                0.455393
Inwood, NYC                           0.455195
Ocean Hill, NYC                       0.454372
Bedford Park, NYC                     0.454209
Gramercy Park, NYC                    0.453847
Howard Beach, NYC                     0.453234
Yorkville, NYC                        0.452182
Sunnyside, NYC                        0.451711
Fort Hamilton, NYC                    0.451711
Madison, NYC                          0.451541
Kips Bay, NYC                         0.451031
Borough Park, NYC                     0.450697
Castleton Corners, NYC                0.450680
East Village, NYC                     0.448211
Hamilton Heights, NYC                 0.447912
Randa

In [523]:
neighborhood = 'SoHo, NYC'
ranked = Similarity[[neighborhood]].sort_values(by=neighborhood)[::-1]
ranked[['Chicago' in x for x in ranked.index]]

City, Neighborhood                         SoHo, NYC
City, Neighborhood                                  
Cabrini–Green, Chicago                      0.650673
Park West, Chicago                          0.646383
Wrigleyville, Chicago                       0.639735
Lake View East, Chicago                     0.639070
Lake View, Chicago                          0.639070
West Lakeview, Chicago                      0.638495
Lakewood, Chicago                           0.614691
Little Italy, Chicago                       0.603481
Bucktown, Chicago                           0.599123
Graceland West, Chicago                     0.592751
Polish Village, Chicago                     0.591864
West DePaul, Chicago                        0.591257
Wicker Park, Chicago                        0.590802
Greektown, Chicago                          0.589980
Near North Side, Chicago                    0.587969
Boystown, Chicago                           0.581818
Pulaski Park, Chicago                       0.581105
Lincoln Park, Chicago                       0.579751
Noble Square, Chicago                       0.570145
Belmont Terrace, Chicago                    0.569558
Belmont Gardens, Chicago                    0.569558
Belmont Central, Chicago                    0.569558
Gold Coast, Chicago                         0.564463
Near West Side, Chicago                     0.562183
Edgewater Beach, Chicago                    0.556553
Edgewater, Chicago                          0.556553
Edison Park, Chicago                        0.553974
Old Town, Chicago                           0.553638
West Town, Chicago                          0.550000
Goose Island, Chicago                       0.541616
Sheridan Park, Chicago                      0.541083
North Center, Chicago                       0.539608
The Gap, Chicago                            0.535406
Nortown, Chicago                            0.533163
Roscoe Village, Chicago                     0.531625
Jackson Park, Chicago                       0.527081
Union Ridge, Chicago                        0.526890
Buena Park, Chicago                         0.526870
Hyde Park, Chicago                          0.526004
East Hyde Park, Chicago                     0.526004
North Kenwood, Chicago                      0.525885
Kenwood, Chicago                            0.525885
Fulton River District, Chicago              0.522459
Parkview, Chicago                           0.522248
Merchant Park, Chicago                      0.521538
Irving Park, Chicago                        0.518022
Old Irving Park, Chicago                    0.518022
Little Village, Chicago                     0.509432
West Loop, Chicago                          0.509432
The Villa, Chicago                          0.509432
East Village, Chicago                       0.509432
The Loop, Chicago                           0.509432
The Island, Chicago                         0.509432
River West, Chicago                         0.509432
Palmer Square, Chicago                      0.508218
Logan Square, Chicago                       0.506286
Tri-Taylor, Chicago                         0.505400
Avondale Gardens, Chicago                   0.505051
Avondale, Chicago                           0.505051
Jackowo, Chicago                            0.505051
Magnificent Mile, Chicago                   0.503461
Streeterville, Chicago                      0.500184
Printer's Row, Chicago                      0.499826
Cottage Grove, Chicago                      0.497814
Ukrainian Village, Chicago                  0.488795
Dearborn Park, Chicago                      0.488693
Kosciuszko Park, Chicago                    0.486369
Edgewater Glen, Chicago                     0.485963
River North, Chicago                        0.485291
Bowmanville, Chicago                        0.483065
Kilbourn Park, Chicago                      0.475385
West Woodlawn, Chicago                      0.474687
Woodlawn, Chicago                           0.474687
Mayfair, Chicago         

# The results look good to me based on my experience with both cities. But I do recommend that you try it out for yourself. Below is a function that will map neighborhoods in New York or Chicago based on a favorite neighborhood in the other city

In [583]:
import matplotlib.pyplot as plt
import matplotlib.colors as color
def map_recommendations(fave_neighb, city_of_interest):
    #ranked = Similarity[[fave_neighb]].sort_values(by=fave_neighb)[::-1]
    #ranked[[city_of_interest in x for x in ranked.index]]
    #rankings = ranked[fave_neighb].tolist()
    # create map
    loc = geolocator.geocode(city_of_interest +', USA')
    latitude = loc.latitude
    longitude = loc.longitude
    map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

    # add markers to the map
    markers_colors = []
    for lat, lon, poi, r in zip(Clusters_of_neighborhoods['Latitude'], Clusters_of_neighborhoods['Longitude'], Clusters_of_neighborhoods['City, Neighborhood'], Similarity[[fave_neighb]][fave_neighb].tolist()):
        label = folium.Popup(str(poi) + ' Similarity index ' + str(r), parse_html=True)
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            color=color.to_hex(plt.cm.RdYlGn(r)),
            fill=True,
            fill_color=color.to_hex(plt.cm.RdYlGn(r)),
            fill_opacity=0.7).add_to(map_clusters)

    return map_clusters

## Below are some examples
Neighborhoods similar to Wicker Park in NY

In [584]:
map_recommendations('Wicker Park, Chicago', 'NYC')

Neighborhoods similar to SoHo in NY

In [587]:
map_recommendations('SoHo, NYC', 'NYC')

Neighborhoods similar to SoHo in Chicago

In [588]:
map_recommendations('SoHo, NYC', 'Chicago')